In [14]:
%cd "D:\Akash\Work\AI\model_evaluation\yolov5\"

D:\Akash\Work\AI\model_evaluation\yolov5


In [15]:
import os
import shutil
import logging
import pandas as pd
from openpyxl import load_workbook
from importlib import reload
import detect
import argparse
from enum import Enum
reload(logging)

logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s: %(message)s')
class PredictionData:
    '''
    defines the folder structure of the prediction data
    1_HBI(202403)+person
            ->labels
                ->raw_test_5_0.txt
                ->raw_test_5_1.txt
                ->...
            ->images 
                ->raw_test_5_0.jpg
                ->raw_test_5_1.jpg
                ->...
    '''
    def __init__(self, path, name):
        self.model_name = name
        self.path = os.path.join(path, self.model_name)
        if not os.path.exists(self.path):
            logging.error(fr"Path: {self.path} does not exist")
            raise Exception(fr"Prediction data {name} not found")
        self.label_dir = os.path.join(self.path, r"labels")
        self.image_dir = os.path.join(self.path, r"images")
        if not os.path.exists(self.label_dir):
            logging.error(fr"Labels folder : {self.label_dir} does not exist")
            raise Exception("Labels folder not found")
        self.label_files = set([file for file in os.listdir(self.label_dir) if file.endswith('.txt')])
        logging.info(fr'Total of {len(self.label_files)} predictions found for model {self.model_name}... ')
class EvaluationData:
    '''
    defines the folder structure of the evaluation data
    1_HBI(202403)+person
            ->labels
                ->raw_test_5_0.txt
                ->raw_test_5_1.txt
                ->...
            ->images 
                ->raw_test_5_0.jpg
                ->raw_test_5_1.jpg
                ->...
    '''
    def __init__(self,path, name):
        self.name = name
        # self.path = os.path.join(path, self.name)
        self.path = path
        if not os.path.exists(self.path):
            logging.error(fr"Path: {self.path} does not exist")
            raise Exception(fr"Evaluation data {self.name} not found")
        self.image_dir = os.path.join(self.path, r"images")
        self.label_dir = os.path.join(self.path, r"labels")
        
        if not os.path.exists(self.image_dir):
            logging.error(fr"Image folder : {self.image_dir} does not exist")
            raise Exception(fr"Image folder not found for {self.name}")
        if not os.path.exists(self.label_dir):
            logging.error(fr"Labels folder : {self.label_dir} does not exist")
            raise Exception(fr"Labels folder not found for {self.name}")
        self.image_files = set([file for file in os.listdir(self.image_dir) if file.endswith(('.jpg'))])
        self.label_files = set([file for file in os.listdir(self.label_dir) if file.endswith('.txt')])
        self.get_TN_names()
        logging.info(fr'For {self.name}: Images: {len(self.image_files)}, Annotation : {len(self.label_files)}... ')
    def get_TN_names(self):
        image_names = set(x.split(".")[0] for x in self.image_files)
        labels_names= set(x.split(".")[0] for x in self.label_files)
        background = image_names.difference(labels_names)
        self.background = set(x+".txt" for x in background)
        

In [16]:
class ExcelFile:
    headers = ['Model name', 'FP', 'FN', 'BB_error', 'TP', 'TN']

    def __init__(self, path, sheets_names):
        self.create_excel_file(path, sheets_names)

    def create_excel_file(self, path, sheets_names):
        self.excel_path = os.path.join(path, 'results.xlsx')
        self.writer = pd.ExcelWriter(self.excel_path, engine='openpyxl')
        for sheet_name in sheets_names:
            df = pd.DataFrame(columns=ExcelFile.headers)
            df.to_excel(self.writer, sheet_name=sheet_name, index=False)
        self.writer.close()

    def add_data_to_sheet(self, sheet_name, data):
        book = load_workbook(self.excel_path)
        with pd.ExcelWriter(self.excel_path, engine='openpyxl', mode='a', if_sheet_exists='overlay') as writer:
            writer._book = book
            writer._sheets = {ws.title: ws for ws in book.worksheets}

            # Ensure data is in the correct format (as a list of dictionaries for each row)
            data_dict = [{ExcelFile.headers[i]: val for i, val in enumerate(data)}]
            df = pd.DataFrame(data_dict)

            start_row = book[sheet_name].max_row if book[sheet_name].max_row > 1 else 0
            df.to_excel(writer, sheet_name=sheet_name, index=False, header=False if start_row else True, startrow=start_row)  
            
class ResultFolder:
    '''
    This class is used to represent the structure of the result folder 
    The structure is 
    Result folder
        ->results.txt
        ->results_BB_error.txt
        ->results_FP.txt
        ->results_FN.txt
        ->BB_Error
            ->images
                ->raw_test_5_0.jpg
                ->raw_test_5_5.jpg
                ->........
            ->labels
                ->classes.txt
                ->raw_test_5_0.txt
                ->raw_test_5_5.txt
                ->........
        ->FN
            ->images
                ->raw_test_5_0.jpg
                ->raw_test_5_5.jpg
                ->........
            ->labels
                ->classes.txt
                ->raw_test_5_0.txt
                ->raw_test_5_5.txt
                ->........
        ->FP
            ->images
                ->raw_test_5_0.jpg
                ->raw_test_5_5.jpg
                ->........
            ->labels
                ->classes.txt
                ->raw_test_5_0.txt
                ->raw_test_5_5.txt
                ->........
    '''
    RESULTS = 1
    FN=2
    FP=3
    BB_ERROR = 4
    TP = 5
    TN = 6 
    def __init__(self, save_path):
        self.fn_folder_path = os.path.join(save_path, r"FN")#stores the FN
        self.fp_folder_path = os.path.join(save_path, r"FP")#stores the FP
        self.bb_error_folder_path = os.path.join(save_path, r"BB_error")#stores the BB error
        self.tp_folder_path = os.path.join(save_path, r"TP")#stores the TP
        self.tn_folder_path = os.path.join(save_path, r"TN")#stores the TN 
        #create directories
        for path in [self.fn_folder_path, self.fp_folder_path, self.bb_error_folder_path, self.tp_folder_path, self.tn_folder_path]:
            if os.path.exists(path):
                shutil.rmtree(path)
            os.makedirs(path, exist_ok=True)
        #images and label paths
        self.tn_images_path, _,  self.tn_images_with_BB = self.create_error_folder_format(self.tn_folder_path)
        self.fn_images_path, self.fn_labels_path, self.fn_images_with_BB = self.create_error_folder_format(self.fn_folder_path)
        self.fp_images_path, self.fp_labels_path, self.fp_images_with_BB = self.create_error_folder_format(self.fp_folder_path)
        self.tp_images_path, self.tp_labels_path,  self.tp_images_with_BB = self.create_error_folder_format(self.tp_folder_path)
        self.bb_error_images_path, self.bb_error_labels_path,  self.bb_error_images_with_BB = self.create_error_folder_format(self.bb_error_folder_path)
        #results file path
        self.fn_file_path = os.path.join(save_path,       r"results_FN.txt")#stores the FN image numbers
        self.fp_file_path = os.path.join(save_path,       r"results_FP.txt")#stores the FP image numbers
        self.bb_error_file_path = os.path.join(save_path, r"results_BB_error.txt")#stores the BB error image numbers
        self.results_file_path = os.path.join(save_path,  r"results.txt")#save all 3 errors count 
        self.tp_file_path = os.path.join(save_path,       r"results_TP.txt")
        self.tn_file_path = os.path.join(save_path,       r"results_TN.txt")
        for path in [self.fn_file_path, self.fp_file_path, self.bb_error_file_path, self.results_file_path, self.tp_file_path, self.tn_file_path]:
            if os.path.exists(path):
                os.remove(path)
    
    def create_error_folder_format(self, folder_path, labels = r'person'):
        images_path, labels_path, images_withBB_path =  os.path.join(folder_path,r"images"), os.path.join(folder_path,r"labels"),  os.path.join(folder_path,r"images_withBB")
        for path in [images_path, labels_path, images_withBB_path]:
            os.makedirs(path, exist_ok=True)
        self.create_classestxt_file(labels_path, labels)
        return images_path, labels_path, images_withBB_path
    
    def create_classestxt_file(self, path, data):
        '''
        Creates classes txt
        '''
        with open(os.path.join(path, "classes.txt"), "w") as file:
            file.write(data)
    def write_results(self,file_type, string):
        path = ''
        if file_type == ResultFolder.RESULTS:
            path = self.results_file_path
        elif file_type == ResultFolder.FN:
            path = self.fn_file_path
        elif file_type == ResultFolder.FP:
            path = self.fp_file_path
        elif file_type == ResultFolder.BB_ERROR:
            path = self.bb_error_file_path
        elif file_type == ResultFolder.TP:
            path = self.tp_file_path
        elif file_type == ResultFolder.TN:
            path = self.tn_file_path
        with open(path, "a") as file_results:
            file_results.write(string)
    def add_to_label_file(self, file_path, info):
    # Open the file in append mode, which creates the file if it doesn't exist
        with open(file_path, 'a') as file:
            for line in info:
                file.write('0 '+' '.join(map(str, line)) + '\n')
    def save_results(self, matched_pred, unmatched_gt, unmatched_pred, bbox_error, filename, gt_image_path, pred_img_path):
        tp_count = len(matched_pred)
        fn_count = len(unmatched_gt)
        fp_count = len(unmatched_pred)
        bb_error_count = len(bbox_error)
        image_number = filename.split('.')[0]
        if tp_count > 0:
            self.write_results(ResultFolder.TP, f"{image_number}: TPs={tp_count}\n")
            # self.add_to_label_file(os.path.join(self.tp_labels_path, filename),matched_pred)
            # self.copy_image(gt_image_path, os.path.join(self.tp_images_path, image_number + ".jpg"))
            # self.copy_image(pred_img_path, os.path.join(self.tp_images_with_BB, image_number + ".jpg"))
        # if fp_count > 0:
            # self.write_results(ResultFolder.FP, f"{image_number}: FPs={fp_count}\n")
            # self.add_to_label_file(os.path.join(self.fp_labels_path, filename),unmatched_pred)
            # self.copy_image(gt_image_path, os.path.join(self.fp_images_path, image_number + ".jpg"))
            # self.copy_image(pred_img_path, os.path.join(self.fp_images_with_BB, image_number + ".jpg"))
        # if fn_count > 0:
            # self.write_results(ResultFolder.FN, f"{image_number}: FNs={fn_count}\n")
            # self.add_to_label_file(os.path.join(self.fn_labels_path, filename), unmatched_gt)
            # self.copy_image(gt_image_path, os.path.join(self.fn_images_path, image_number + ".jpg"))
            # self.copy_image(pred_img_path, os.path.join(self.fn_images_with_BB, image_number + ".jpg"))
        # if bb_error_count > 0:
            # self.write_results(ResultFolder.BB_ERROR, f"{image_number}: BB_error={bb_error_count}\n")
            # self.add_to_label_file(os.path.join(self.bb_error_labels_path, filename), bbox_error)
            # self.copy_image(gt_image_path, os.path.join(self.bb_error_images_path, image_number + ".jpg"))
            # self.copy_image(pred_img_path, os.path.join(self.bb_error_images_with_BB, image_number + ".jpg"))
  
    def copy_image(self,source, destination):
        shutil.copyfile(source, destination)   
    def copy_tn(self, tn_names, source):
        for name in tn_names:
            file_name = name.split('.')[0]  + ".jpg"
            self.write_results(ResultFolder.TN, f"{file_name}: TNs={1}\n")
            #os.path.join(evaluation_data.image_dir, image_number + ".jpg")
            shutil.copyfile(os.path.join(source, file_name), os.path.join(self.tn_images_path, file_name))

    def save_labels(self, file_path, info):
        with open(file_path, 'a') as file:
            for line in info:
                file.write("".join([label.get_YOLO_format() for label in info]))
                import os

def calculate_iou(box1, box2,filename):
    """
    Calculate Intersection over Union (IoU) between two bounding boxes in YOLO format.
    """
    if not box1 or not box2:
        print(filename,"Has empty box")
        return 0.0
    x1, y1, w1, h1 = box1
    x2, y2, w2, h2 = box2

    # Calculate coordinates of bounding box corners
    x1_left, y1_top = x1 - w1 / 2, y1 - h1 / 2
    x1_right, y1_bottom = x1 + w1 / 2, y1 + h1 / 2
    x2_left, y2_top = x2 - w2 / 2, y2 - h2 / 2
    x2_right, y2_bottom = x2 + w2 / 2, y2 + h2 / 2

    # Calculate intersection area
    x_overlap = max(0, min(x1_right, x2_right) - max(x1_left, x2_left))
    y_overlap = max(0, min(y1_bottom, y2_bottom) - max(y1_top, y2_top))
    intersection_area = x_overlap * y_overlap

    # Calculate union area
    box1_area = w1 * h1
    box2_area = w2 * h2
    union_area = box1_area + box2_area - intersection_area

    # Calculate IoU
    iou = intersection_area / union_area if union_area > 0 else 0
    return iou
    
def match_instances(ground_truth, predicted,filename, iou_threshold=0.5,bounding_box_threshold=0.7):
    """
    Match instances based on IoU.
    """
    matched_gt, matched_pred, bbox_error, unmatched_gt, unmatched_pred = [], [],[], ground_truth.copy(), predicted.copy()

    for i, gt_box in enumerate(ground_truth):
        max_iou = 0
        max_iou_idx = -1
        for j, pred_box in enumerate(predicted):
            
            
            iou = calculate_iou(gt_box, pred_box,filename)
            
            if iou > max_iou:
                max_iou = iou
                max_iou_idx = j
                
        if max_iou > iou_threshold:
            if(iou_threshold<max_iou<=bounding_box_threshold):
               bbox_error.append(predicted[max_iou_idx])
            matched_gt.append(ground_truth[i])
            matched_pred.append(predicted[max_iou_idx])
            unmatched_gt.remove(ground_truth[i])
            unmatched_pred.pop(max_iou_idx)
            predicted.pop(max_iou_idx)

    return matched_gt, matched_pred, unmatched_gt, unmatched_pred,bbox_error

def read_label_data(path):
    data = []
    if os.path.exists(path):
        with open(path, 'r') as f:
            lines_gt = f.readlines()
        for line in lines_gt:
            elements = line.strip().split()
            if len(elements) == 5 :  # YOLO format has 5 elements
                data = [list(map(float, line.strip().split()[1:])) for line in lines_gt]
    return data       

def analyse(save_path, evaluation_data:EvaluationData, prediction_data: PredictionData):
    #creating the results folder 
    result_folder = ResultFolder(save_path)
    all_files = evaluation_data.label_files.union(prediction_data.label_files)
    fp_total = fn_total = bb_error_total = tp_total = 0
    #Calculate tn and save Tn 
    tn_files = evaluation_data.background.difference(prediction_data.label_files)
    tn_total = len(tn_files)
    result_folder.copy_tn(tn_files, evaluation_data.image_dir)
    #Calculate fp,tp and fn
    for filename in all_files:
        if filename.endswith(".txt") and filename != "classes.txt":
            gt_path = os.path.join(evaluation_data.label_dir, filename)
            gt_image_path = os.path.join(evaluation_data.image_dir, filename.split('.')[0] + ".jpg")
            pred_path = os.path.join(prediction_data.label_dir, filename)
            pred_img_path = os.path.join(prediction_data.image_dir, filename.split('.')[0] + ".jpg")
            #read the label file data
            ground_truth_boxes = read_label_data(gt_path)
            predicted_boxes = read_label_data(pred_path)
                
            matched_gt, matched_pred, unmatched_gt, unmatched_pred, bbox_error = match_instances(ground_truth_boxes, predicted_boxes, filename, iou_threshold = 0.5,bounding_box_threshold = 0.7)
            tp_total += len(matched_pred)
            fp_total += len(unmatched_pred)
            fn_total += len(unmatched_gt)
            bb_error_total += len(bbox_error)
            #save the results of this label file 
            result_folder.save_results(matched_pred, unmatched_gt, unmatched_pred, bbox_error, filename, gt_image_path, pred_img_path)
    result_folder.write_results(ResultFolder.RESULTS, f"TP_count = {tp_total},\tTN_count = {tn_total},\tFP_count = {fp_total},\tFN_count = {fn_total},\tBB_error_count = {bb_error_total}\n")
    return fp_total, fn_total, bb_error_total, tp_total, tn_total
# -----------------------------------------------Set of functions for merging --------------------------------
def process_folder(folder_path, subfolder_name, class_index, class_data):
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        if file_name.endswith(".txt"):
            with open(file_path, "r") as file:
                lines = file.readlines()
            for line in lines:
                parts = line.strip().split()
                parts[0] = str(class_index)
                updated_line = " ".join(parts)
                class_data.setdefault((subfolder_name, file_name), []).append(updated_line)

def copy_images(input_dir, output_dir, folder_name, subfolder_name):
    folder_path = os.path.join(input_dir, folder_name, subfolder_name)
    images_folder = os.path.join(folder_path, "images")
    if os.path.isdir(images_folder):
        output_subfolder_dir = os.path.join(output_dir, f"{subfolder_name}_All")
        output_images_folder = os.path.join(output_subfolder_dir, "images")
        os.makedirs(output_images_folder, exist_ok=True)
        for file_name in os.listdir(images_folder):
            file_path = os.path.join(images_folder, file_name)
            if os.path.isfile(file_path):
                output_file_path = os.path.join(output_images_folder, file_name)
                shutil.copy(file_path, output_file_path)

def process_labels(input_dir, output_dir, folder_name, subfolder_name, class_index, class_data):
    folder_path = os.path.join(input_dir, folder_name, subfolder_name)
    labels_folder = os.path.join(folder_path, "labels")
    if os.path.isdir(labels_folder):
        output_subfolder_dir = os.path.join(output_dir, f"{subfolder_name}_All")
        output_labels_folder = os.path.join(output_subfolder_dir, "labels")
        os.makedirs(output_labels_folder, exist_ok=True)
        process_folder(labels_folder, subfolder_name, class_index, class_data)

def merge_data(input_dir, output_dir):
    class_data = {}
    folders = sorted(folder for folder in os.listdir(input_dir) if os.path.join(input_dir, folder) != output_dir)
    for i, folder_name in enumerate(folders):
        for subfolder_name in ["BB_error", "FN", "FP"]:
            copy_images(input_dir, output_dir, folder_name, subfolder_name)
            process_labels(input_dir, output_dir, folder_name, subfolder_name, i, class_data)
    for (subfolder_name, class_name), data_lines in class_data.items():
        output_label_folder = os.path.join(output_dir, f"{subfolder_name}_All", "labels")
        output_file_path = os.path.join(output_label_folder, class_name)
        os.makedirs(output_label_folder, exist_ok=True)
        with open(output_file_path, "w") as output_file:
            for line in data_lines:
                output_file.write(line + "\n")

# to update class.txt
def update_classes(output_dir, new_class_names):
    for subfolder_name in ["BB_error_All", "FN_All", "FP_All"]:
        labels_folder = os.path.join(output_dir, subfolder_name, "labels")
        classes_file_path = os.path.join(labels_folder, "classes.txt")
        if os.path.isfile(classes_file_path):
            with open(classes_file_path, "w") as classes_file:
                for class_name in new_class_names:
                    classes_file.write(class_name + "\n")


# fill from here




## fill the model info

In [17]:
import os

def list_files(directory):
    # List all files and directories in the specified directory
    paths = []
    for root, dirs, files in os.walk(directory):
        for file in files:
            # Append the file path to the list
            paths.append(os.path.join(root, file))
    return paths

# Specify the directory path
directory_path = r"D:\Akash\Work\AI\202407_tc1\temp\pt_files"

# Get all file paths
file_paths = list_files(directory_path)
models={}
# print(file_paths)
for x in file_paths:
   models[os.path.basename(x)[:-3]] = x

## fill the test data info

In [18]:
'''
name of the dataset and path , The folder structure should be 
-raw_test_5
    --->images
        --->000000.jpg
    --->labels
        --->000000.txt
'''
extracted_dataset_paths = {
    "結合データセット":                     r"D:\Akash\Work\AI\test_data\datasets\test_data",
    # "ぼやけされている人":                   r"D:\Akash\Work\AI\test_data\datasets\cases\ぼやけされている人",
    # "運転している":                         r"D:\Akash\Work\AI\test_data\datasets\cases\運転している",
    # "顔が見えない運転者の画像":              r"D:\Akash\Work\AI\test_data\datasets\cases\顔が見えない運転者の画像",
    # "屈んでいるポーズ":                     r"D:\Akash\Work\AI\test_data\datasets\cases\屈んでいるポーズ",
    # "座っているポーズ":                     r"D:\Akash\Work\AI\test_data\datasets\cases\座っているポーズ",
    # "遮蔽されている人":                     r"D:\Akash\Work\AI\test_data\datasets\cases\遮蔽されている人",
    # "体の部分":                            r"D:\Akash\Work\AI\test_data\datasets\cases\体の部分",
    # "特徴がよくみえない画像":               r"D:\Akash\Work\AI\test_data\datasets\cases\特徴がよくみえない画像",
    # "背景":                                r"D:\Akash\Work\AI\test_data\datasets\cases\背景",
    # "箱を持っている·運んでいるポーズ":       r"D:\Akash\Work\AI\test_data\datasets\cases\箱を持っている·運んでいるポーズ",
    # "立っているポーズ":                     r"D:\Akash\Work\AI\test_data\datasets\cases\立っているポーズ",
}

In [19]:
# output path , path for saving the results 
'''
The output format is 
raw_test_5
    ->results.txt
    ->results_BB_error.txt
    ->results_FP.txt
    ->results_FN.txt
    ->BB_Error
        ->images
            ->raw_test_5_0.jpg
            ->raw_test_5_5.jpg
            ->........
        ->labels
            ->classes.txt
            ->raw_test_5_0.txt
            ->raw_test_5_5.txt
            ->........
    ->FN
        ->images
            ->raw_test_5_0.jpg
            ->raw_test_5_5.jpg
            ->........
        ->labels
            ->classes.txt
            ->raw_test_5_0.txt
            ->raw_test_5_5.txt
            ->........
    ->FP
        ->images
            ->raw_test_5_0.jpg
            ->raw_test_5_5.jpg
            ->........
        ->labels
            ->classes.txt
            ->raw_test_5_0.txt
            ->raw_test_5_5.txt
            ->........
'''
save_folder = r"D:\Akash\Work\AI\202407_tc1\temp\error_analysis"



In [20]:
import os
import argparse
import detect


def create_config_detect(weights_path, project_path, name, source_path):
    # Creating an argparse.Namespace manually
    opt = argparse.Namespace(
        weights=weights_path,  # model path or triton URL
        source=f"{source_path}/images",  # file/dir/URL/glob/screen/0(webcam)
        data=r"data\coco128.yaml",  # dataset.yaml path                                              
        imgsz=(640, 640),  # inference size (height, width)
        conf_thres=0.25,  # confidence threshold
        iou_thres=0.45,  # NMS IOU threshold
        max_det=1000,  # maximum detections per image
        device="",  # cuda device, i.e. 0 or 0,1,2,3 or cpu
        view_img=False,  # show results
        save_txt=True,  # save results to *.txt
        save_csv=False,  # save results in CSV format
        save_conf=False,  # save confidences in --save-txt labels
        save_crop=False,  # save cropped prediction boxes
        nosave=False,  # do not save images/videos
        classes=0,  # filter by class: --class 0, or --class 0 2 3
        agnostic_nms=False,  # class-agnostic NMS
        augment=False,  # augmented inference
        visualize=False,  # visualize features
        update=False,  # update all models
        project=project_path,  # save results to project/name
        name=name,  # save results to project/name
        exist_ok=False,  # existing project/name ok, do not increment
        line_thickness=3,  # bounding box thickness (pixels)
        hide_labels=False,  # hide labels
        hide_conf=False,  # hide confidences
        half=False,  # use FP16 half-precision inference
        dnn=False,  # use OpenCV DNN for ONNX inference
        vid_stride=1,  # video frame-rate stride
    )
    return opt


In [21]:
import pathlib
pathlib.PosixPath = pathlib.WindowsPath

save_path_base = os.path.join(save_folder, r"detection")
os.makedirs(save_path_base,exist_ok=True)
for dataset_name, data_path in extracted_dataset_paths.items():
    project_path = os.path.join(save_path_base, dataset_name)
    for model_name, model_path in models.items():
        opt_detect = create_config_detect(weights_path=model_path,project_path= project_path, name=model_name, source_path = data_path)
        detect.main(opt_detect)

YOLOv5  2024-8-5 Python-3.8.10 torch-2.4.0+cu124 CUDA:0 (NVIDIA GeForce GTX 1650, 4096MiB)

Fusing layers... 
Model summary: 157 layers, 7012822 parameters, 0 gradients, 15.8 GFLOPs
image 1/17306 D:\Akash\Work\AI\test_data\datasets\test_data\images\raw_test1_000001.jpg: 640x640 (no detections), 40.2ms
image 2/17306 D:\Akash\Work\AI\test_data\datasets\test_data\images\raw_test1_000002.jpg: 640x640 (no detections), 14.0ms
image 3/17306 D:\Akash\Work\AI\test_data\datasets\test_data\images\raw_test1_000003.jpg: 640x640 1 person, 14.0ms
image 4/17306 D:\Akash\Work\AI\test_data\datasets\test_data\images\raw_test1_000004.jpg: 640x640 1 person, 14.0ms
image 5/17306 D:\Akash\Work\AI\test_data\datasets\test_data\images\raw_test1_000005.jpg: 640x640 1 person, 14.0ms
image 6/17306 D:\Akash\Work\AI\test_data\datasets\test_data\images\raw_test1_000006.jpg: 640x640 1 person, 14.0ms
image 7/17306 D:\Akash\Work\AI\test_data\datasets\test_data\images\raw_test1_000007.jpg: 640x640 1 person, 12.0ms
image 

In [22]:
def move_images_to_images_folder(root_folder_path):
    # Walk through the root directory
    for subdir, dirs, files in os.walk(root_folder_path):
        for sub_subdir in dirs:
            sub_subdir_path = os.path.join(subdir, sub_subdir)
            labels_folder_path = os.path.join(sub_subdir_path, "labels")
            
            if os.path.isdir(labels_folder_path):
                # Create the 'images' folder within the same subfolder
                images_folder_path = os.path.join(sub_subdir_path, "images")
                if not os.path.exists(images_folder_path):
                    os.makedirs(images_folder_path)
                
                # Move .jpg files to the 'images' folder
                for file in os.listdir(sub_subdir_path):
                    if file.endswith(".jpg"):
                        file_path = os.path.join(sub_subdir_path, file)
                        shutil.move(file_path, images_folder_path)
                        
                print(f"All images have been moved to {images_folder_path}")
                
root_folder_path = save_path_base
move_images_to_images_folder(root_folder_path)

All images have been moved to D:\Akash\Work\AI\202407_tc1\temp\error_analysis\detection\ぼやけされている人\240727084544_runs_train_2024_07_tc1_dataset_24\images
All images have been moved to D:\Akash\Work\AI\202407_tc1\temp\error_analysis\detection\ぼやけされている人\240727090819_runs_train_2024_07_tc1_dataset_25\images
All images have been moved to D:\Akash\Work\AI\202407_tc1\temp\error_analysis\detection\ぼやけされている人\240727182157_runs_train_2024_07_tc1_dataset_26\images
All images have been moved to D:\Akash\Work\AI\202407_tc1\temp\error_analysis\detection\体の部分\240727084544_runs_train_2024_07_tc1_dataset_24\images
All images have been moved to D:\Akash\Work\AI\202407_tc1\temp\error_analysis\detection\体の部分\240727090819_runs_train_2024_07_tc1_dataset_25\images
All images have been moved to D:\Akash\Work\AI\202407_tc1\temp\error_analysis\detection\体の部分\240727182157_runs_train_2024_07_tc1_dataset_26\images
All images have been moved to D:\Akash\Work\AI\202407_tc1\temp\error_analysis\detection\屈んでいるポーズ\240727

### Enter the model result save folder

In [23]:
#predicted labels base paths 
"""
should be in the format of 
raw_test_5
    ->1_HBI(202403)+person
        ->labels
            ->raw_test_5_0.txt
            ->raw_test_5_1.txt
            ->...
    ->2_HBI(202403)+forklift
        ->labels
                ->raw_test_5_0.txt
                ->raw_test_5_1.txt
                ->...
"""
# pred_path_base = detect_path
pred_path_base = save_path_base

In [24]:
# output path , path for saving the results 
'''
The output format is 
raw_test_5
    ->results.txt
    ->results_BB_error.txt
    ->results_FP.txt
    ->results_FN.txt
    ->BB_Error
        ->images
            ->raw_test_5_0.jpg
            ->raw_test_5_5.jpg
            ->........
        ->labels
            ->classes.txt
            ->raw_test_5_0.txt
            ->raw_test_5_5.txt
            ->........
    ->FN
        ->images
            ->raw_test_5_0.jpg
            ->raw_test_5_5.jpg
            ->........
        ->labels
            ->classes.txt
            ->raw_test_5_0.txt
            ->raw_test_5_5.txt
            ->........
    ->FP
        ->images
            ->raw_test_5_0.jpg
            ->raw_test_5_5.jpg
            ->........
        ->labels
            ->classes.txt
            ->raw_test_5_0.txt
            ->raw_test_5_5.txt
            ->........
'''

save_path_analysis = os.path.join(save_folder, r"error_analysis_results_stats")
os.makedirs(save_path_analysis,exist_ok=True)


In [25]:
model_names = list(models.keys())
model_names.sort()
excel_file = ExcelFile(save_path_analysis, extracted_dataset_paths.keys())
for dataset_name, dataset_path in extracted_dataset_paths.items():
    evaluation_data = EvaluationData(dataset_path, dataset_name)
    save_dataset_root_path = os.path.join(save_path_analysis, dataset_name)
    for model_name in model_names:
        pred_dataset_root_path = os.path.join(pred_path_base, dataset_name)
        prediction_data = PredictionData(pred_dataset_root_path, model_name)
        save_path = os.path.join(save_dataset_root_path, model_name)
        if os.path.exists(save_path):
            shutil.rmtree(save_path)
        os.makedirs(save_path, exist_ok=True)
        fp_total, fn_total, bb_error_total, tp_total, tn_total =  analyse(save_path, evaluation_data, prediction_data)
        data = [model_name, fp_total, fn_total, bb_error_total, tp_total, tn_total]
        excel_file.add_data_to_sheet(dataset_name, data)
    # to merge the labels & images    
    # output_path = os.path.join(save_dataset_root_path, r"Merged")
    # os.makedirs(output_path, exist_ok=True)
    
    # merge_data(save_dataset_root_path, output_path)
    # update_classes(output_path, model_names)
        
    print(fr"Error analysis for {dataset_name} is completed.")

2024-08-06 15:14:51,345 - INFO: For 結合データセット: Images: 17306, Annotation : 14025... 
2024-08-06 15:14:51,353 - INFO: Total of 12519 predictions found for model 240727084544_runs_train_2024_07_tc1_dataset_24... 
2024-08-06 15:15:13,419 - INFO: Total of 12488 predictions found for model 240727090819_runs_train_2024_07_tc1_dataset_25... 
2024-08-06 15:15:23,700 - INFO: Total of 12598 predictions found for model 240727182157_runs_train_2024_07_tc1_dataset_26... 


Error analysis for 結合データセット is completed.


In [26]:
import os
import shutil

def copy_results_txt_files(src_dir, dst_dir):
    for root, dirs, files in os.walk(src_dir):
        # Filter for files that match the criteria
        results_txt_files = [file for file in files if file.endswith('.txt') and 'results' in file]
        
        if results_txt_files:
            # Calculate the relative path from the source directory
            relative_path = os.path.relpath(root, src_dir)
            # Calculate the destination directory path
            dest_path = os.path.join(dst_dir, relative_path)
            
            # Create the destination directory if it doesn't exist
            os.makedirs(dest_path, exist_ok=True)
            
            for file in results_txt_files:
                # Construct the full file paths
                src_file = os.path.join(root, file)
                dst_file = os.path.join(dest_path, file)
                
                # Copy the file
                shutil.copy2(src_file, dst_file)
                print(f"Copied {src_file} to {dst_file}")

# change only the source directory to your error analysis results folder that contains the error counts for all cases
source_directory = r"D:\Akash\Work\AI\202407_tc1\temp\error_analysis\error_analysis_results_stats"
destination_directory = r"Z:\AI\research_2023-\FT\_error_analysis_results\結合データセット\TEMP"
copy_results_txt_files(source_directory, destination_directory)

Copied D:\Akash\Work\AI\202407_tc1\temp\error_analysis\error_analysis_results_stats\ぼやけされている人\240727084544_runs_train_2024_07_tc1_dataset_24\results.txt to Z:\AI\research_2023-\FT\_error_analysis_results\結合データセット\TEMP\ぼやけされている人\240727084544_runs_train_2024_07_tc1_dataset_24\results.txt
Copied D:\Akash\Work\AI\202407_tc1\temp\error_analysis\error_analysis_results_stats\ぼやけされている人\240727084544_runs_train_2024_07_tc1_dataset_24\results_BB_error.txt to Z:\AI\research_2023-\FT\_error_analysis_results\結合データセット\TEMP\ぼやけされている人\240727084544_runs_train_2024_07_tc1_dataset_24\results_BB_error.txt
Copied D:\Akash\Work\AI\202407_tc1\temp\error_analysis\error_analysis_results_stats\ぼやけされている人\240727084544_runs_train_2024_07_tc1_dataset_24\results_FN.txt to Z:\AI\research_2023-\FT\_error_analysis_results\結合データセット\TEMP\ぼやけされている人\240727084544_runs_train_2024_07_tc1_dataset_24\results_FN.txt
Copied D:\Akash\Work\AI\202407_tc1\temp\error_analysis\error_analysis_results_stats\ぼやけされている人\240727084544_runs_tra

# Deleting Raw images and contents of TP folders

In [27]:
import os
import shutil

def delete_images_and_tp_contents(root_path):
    for dirpath, dirnames, filenames in os.walk(root_path):
        # Delete 'images' folders
        if 'images' in dirnames:
            images_path = os.path.join(dirpath, 'images')
            shutil.rmtree(images_path)
            print(f"Deleted folder: {images_path}")
        
        # Delete contents of 'TP' folders but keep the folder
        if 'TP' in dirnames:
            tp_path = os.path.join(dirpath, 'TP')
            for filename in os.listdir(tp_path):
                file_path = os.path.join(tp_path, filename)
                if os.path.isfile(file_path) or os.path.islink(file_path):
                    os.unlink(file_path)
                elif os.path.isdir(file_path):
                    shutil.rmtree(file_path)
            print(f"Deleted contents of folder: {tp_path}")

# Replace 'root_path' with the path to your root folder
root_path = r"D:\Akash\Work\AI\202407_tc1\error_analysis_stats\error_analysis_results_stats"
delete_images_and_tp_contents(root_path)


Deleted contents of folder: D:\Akash\Work\AI\202407_tc1\error_analysis_stats\error_analysis_results_stats\ぼやけされている人\240802155441_runs_train_2024_07_tc1_dataset_2\TP
Deleted contents of folder: D:\Akash\Work\AI\202407_tc1\error_analysis_stats\error_analysis_results_stats\ぼやけされている人\240802190851_runs_train_2024_07_tc1_dataset_1\TP
Deleted contents of folder: D:\Akash\Work\AI\202407_tc1\error_analysis_stats\error_analysis_results_stats\ぼやけされている人\240804072621_runs_train_2024_07_tc1_dataset_3\TP
Deleted contents of folder: D:\Akash\Work\AI\202407_tc1\error_analysis_stats\error_analysis_results_stats\体の部分\240802155441_runs_train_2024_07_tc1_dataset_2\TP
Deleted contents of folder: D:\Akash\Work\AI\202407_tc1\error_analysis_stats\error_analysis_results_stats\体の部分\240802190851_runs_train_2024_07_tc1_dataset_1\TP
Deleted contents of folder: D:\Akash\Work\AI\202407_tc1\error_analysis_stats\error_analysis_results_stats\体の部分\240804072621_runs_train_2024_07_tc1_dataset_3\TP
Deleted contents of folde

# To make just the results excel file

In [28]:
%pip install xlsxwriter

Note: you may need to restart the kernel to use updated packages.


You should consider upgrading via the 'd:\Akash\Work\AI\model_evaluation\evaluation\Scripts\python.exe -m pip install --upgrade pip' command.


In [29]:
import os
import pandas as pd

def read_results(file_path):
    """Read the results.txt file and extract the required values."""
    results = {}
    with open(file_path, 'r') as file:
        line = file.readline().strip()
        pairs = line.split(',')  # Split by comma
        for pair in pairs:
            if '=' in pair:
                key, value = pair.split('=', 1)  # Split only on the first '='
                key = key.strip().replace('_count', '')  # Remove '_count'
                results[key] = int(value.strip())
    return results

def create_error_analysis_excel(root_folder, output_file=None):
    if output_file is None:
        output_file = os.path.join(root_folder, 'error_analysis.xlsx')
    
    try:
        writer = pd.ExcelWriter(output_file, engine='xlsxwriter')
    except ModuleNotFoundError:
        writer = pd.ExcelWriter(output_file)  # Default writer engine

    for subfolder in os.listdir(root_folder):
        subfolder_path = os.path.join(root_folder, subfolder)
        if os.path.isdir(subfolder_path):
            data = []
            columns = ['Model Name', 'FP', 'FN', 'BB_error', 'TP', 'TN']

            for model_folder in os.listdir(subfolder_path):
                model_folder_path = os.path.join(subfolder_path, model_folder)
                if os.path.isdir(model_folder_path):
                    model_name = model_folder
                    results_file = os.path.join(model_folder_path, 'results.txt')
                    
                    if os.path.isfile(results_file):
                        results = read_results(results_file)
                        row = [model_name] + [results.get(col, None) for col in columns[1:]]
                        data.append(row)

            df = pd.DataFrame(data, columns=columns)
            df.to_excel(writer, sheet_name=subfolder, index=False)

    writer.close()

# Example usage
root_folder = r"D:\Akash\Work\AI\New_similarity_range_analysis\error_analysis\error_analysis_results_stats"
create_error_analysis_excel(root_folder)


OSError: Cannot save file into a non-existent directory: 'D:\Akash\Work\AI\New_similarity_range_analysis\error_analysis\error_analysis_results_stats'